# 사용할 라이브러리 로딩

In [1]:
import numpy as np # Numpy
import pandas as pd # Pandas
import matplotlib as mpl #Matplotlib 세팅용
import matplotlib.pyplot as plt # 시각화 도구
import seaborn as sns # 시각화 도구
from sklearn.model_selection import train_test_split # 데이터셋 분리
from sklearn.model_selection import KFold # KFold 교차검증
from sklearn.cluster import KMeans # 클러스터링
from sklearn.metrics import silhouette_score # 실루엣 점수
import xgboost as xgb # XGBoost
from sklearn.model_selection import GridSearchCV # 그리드 서치
from sklearn.metrics import accuracy_score, precision_score # 평가 지표
from sklearn.metrics import recall_score, confusion_matrix, roc_auc_score, f1_score # 평가 지표
from imblearn.combine import SMOTEENN, SMOTETomek # 복합샘플링
from hyperopt import hp, fmin, tpe, Trials # HyperOPT

import warnings # 경고문 제거용


%matplotlib inline
%config Inlinebackend.figure_format = 'retina'

# 한글 폰트 설정
mpl.rc('font', family='D2Coding')
# 유니코드에서 음수 부호 설정
mpl.rc('axes', unicode_minus = False)

warnings.filterwarnings('ignore')
sns.set(font="D2Coding", rc={"axes.unicode_minus":False}, style='darkgrid')
plt.rc('figure', figsize=(10,8))

# 데이터 로딩

In [2]:
data = pd.read_csv('train.csv')

## 데이터 탐색

In [3]:
data.head()

PassengerId HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck               Name  \
0          0.0        0.0           0.0     0.0     0.0    Maham Ofracculy   
1        109.0        9.0          25.0   549.0    44.0       Juanna Vines   
2         43.0     3576.0           0.0  6715.0    49.0      Altark Susent   
3          0.0     1283.0         371.0  3329.0   193.0       Solam Susent   
4        303.0       70.0         151.0   565.0     2.0  Willy Santantines   

   Transported  
0        False  
1         True  
2        False  
3        False  
4         True

In [4]:
data.columns

Index(['PassengerId', 'HomePlanet', 'CryoSleep', 'Cabin', 'Destination', 'Age',
       'VIP', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck',
       'Name', 'Transported'],
      dtype='object')

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   8693 non-null   object 
 1   HomePlanet    8492 non-null   object 
 2   CryoSleep     8476 non-null   object 
 3   Cabin         8494 non-null   object 
 4   Destination   8511 non-null   object 
 5   Age           8514 non-null   float64
 6   VIP           8490 non-null   object 
 7   RoomService   8512 non-null   float64
 8   FoodCourt     8510 non-null   float64
 9   ShoppingMall  8485 non-null   float64
 10  Spa           8510 non-null   float64
 11  VRDeck        8505 non-null   float64
 12  Name          8493 non-null   object 
 13  Transported   8693 non-null   bool   
dtypes: bool(1), float64(6), object(7)
memory usage: 891.5+ KB


In [6]:
data.isna().sum()

PassengerId       0
HomePlanet      201
CryoSleep       217
Cabin           199
Destination     182
Age             179
VIP             203
RoomService     181
FoodCourt       183
ShoppingMall    208
Spa             183
VRDeck          188
Name            200
Transported       0
dtype: int64

## Cabin 결측값 처리
- 결측값 확인 후 우선 Cabin부터 채워넣기로 함
- PassengerId의 첫 4자리 숫자는 승객의 그룹을 의미함으로 Cabin 결측값 중 그룹이 있으면 그룹의 Cabin으로 채워넣음
- train뿐만 아니라 test에도 결측값이 있기에 같이 처리하기로 함
- 그렇게 처리하고 나온 파일이 하단의 파일

In [120]:
data = pd.read_excel('train_test_origin.xlsx')

In [8]:
data.head()

PassengerId HomePlanet  CryoSleep Cabin1  Cabin2 Combi Cabin3  Cabin  \
0     0001_01     Europa      False      B     0.0    B0      P  B/0/P   
1     0002_01      Earth      False      F     0.0    F0      S  F/0/S   
2     0003_01     Europa      False      A     0.0    A0      S  A/0/S   
3     0003_02     Europa      False      A     0.0    A0      S  A/0/S   
4     0004_01      Earth      False      F     1.0    F1      S  F/1/S   

   Destination   Age  VIP  RoomService  FoodCourt  ShoppingMall     Spa  \
0  TRAPPIST-1e  39.0  0.0          0.0        0.0           0.0     0.0   
1  TRAPPIST-1e  24.0  0.0        109.0        9.0          25.0   549.0   
2  TRAPPIST-1e  58.0  1.0         43.0     3576.0           0.0  6715.0   
3  TRAPPIST-1e  33.0  0.0          0.0     1283.0         371.0  3329.0   
4  TRAPPIST-1e  16.0  0.0        303.0       70.0         151.0   565.0   

   VRDeck               Name  Transported  
0     0.0    Maham Ofracculy          0.0  
1    44.0       Juanna Vines          1.0  
2    49.0      Altark Susent          0.0  
3   193.0       Solam Susent          0.0  
4     2.0  Willy Santantines          1.0

In [9]:
# 결측값을 처리하면 Cabin을 나눠서 구분함
# Cabin은 섹터/방번호/측면으로 구분되어 있음
# Cabin1은 섹터
# Cabin2는 방번호
# Combi는 Cabin1+Cabin2
# Cabin3는 측면(P(ort)는 좌현, S(tarboard)는 우현)
data.columns

Index(['PassengerId', 'HomePlanet', 'CryoSleep', 'Cabin1', 'Cabin2', 'Combi',
       'Cabin3', 'Cabin', 'Destination', 'Age', 'VIP', 'RoomService',
       'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Name', 'Transported'],
      dtype='object')

In [10]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 18 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   12970 non-null  object 
 1   HomePlanet    12691 non-null  object 
 2   CryoSleep     12970 non-null  bool   
 3   Cabin1        12804 non-null  object 
 4   Cabin2        12804 non-null  float64
 5   Combi         12804 non-null  object 
 6   Cabin3        12804 non-null  object 
 7   Cabin         12804 non-null  object 
 8   Destination   12704 non-null  object 
 9   Age           12700 non-null  float64
 10  VIP           12674 non-null  float64
 11  RoomService   12776 non-null  float64
 12  FoodCourt     12752 non-null  float64
 13  ShoppingMall  12760 non-null  float64
 14  Spa           12754 non-null  float64
 15  VRDeck        12766 non-null  float64
 16  Name          12676 non-null  object 
 17  Transported   8693 non-null   float64
dtypes: bool(1), float64(9), ob

- test 데이터는 Kaggle에 제출해야하는 데이터이기에 target인 Transported가 전부 결측임

In [121]:
data.isna().sum()

PassengerId        0
HomePlanet       279
CryoSleep        310
Cabin1           166
Cabin2           166
Combi            166
Cabin3           166
Cabin            166
Destination      266
Age              270
VIP              296
RoomService      194
FoodCourt        218
ShoppingMall     210
Spa              216
VRDeck           204
Name             294
Transported     4277
dtype: int64

- 나머지 결측값을 처리하기 위해 클러스터링을 해보기로 함
- 클러스터링 하기 전에 전처리를 진행해야함

# 전처리

## 필요없는 feature 제거

In [12]:
# 분류하는데 필요없다고 예상되는 'PassengerId', 'Name' feature 제거
data.drop(['PassengerId', 'Name'], inplace=True, axis=1)

In [13]:
# 제거 확인
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12804 non-null  object 
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12674 non-null  float64
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: bool(1), float64(9), object(6)
memory usage: 1.5+ MB


## CryoSleep, VIP, Cabin3 boolean 타입으로 캐스팅

In [14]:
# Cabin3의 P(좌현)를 False으로 S(우현)를 True로 변경
data['Cabin3'].replace({'P': True,'S': False}, inplace=True)

In [15]:
# boolean으로 변환
data['CryoSleep'] = data['CryoSleep'].astype(bool)
data['VIP'] = data['VIP'].astype(bool)
data['Cabin3'] = data['Cabin3'].astype(bool)

In [16]:
# 변환 확인
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: bool(3), float64(8), object(5)
memory usage: 1.3+ MB


In [17]:
# target 값을 제외하고 다른 변수에 저장
df = data.iloc[:,:15]

In [18]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
dtypes: bool(3), float64(7), object(5)
memory usage: 1.2+ MB


## 클러스터링을 위해 다른 결측값들을 전부 제거

In [19]:
df.dropna(inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    11076 non-null  object 
 1   CryoSleep     11076 non-null  bool   
 2   Cabin1        11076 non-null  object 
 3   Cabin2        11076 non-null  float64
 4   Combi         11076 non-null  object 
 5   Cabin3        11076 non-null  bool   
 6   Cabin         11076 non-null  object 
 7   Destination   11076 non-null  object 
 8   Age           11076 non-null  float64
 9   VIP           11076 non-null  bool   
 10  RoomService   11076 non-null  float64
 11  FoodCourt     11076 non-null  float64
 12  ShoppingMall  11076 non-null  float64
 13  Spa           11076 non-null  float64
 14  VRDeck        11076 non-null  float64
dtypes: bool(3), float64(7), object(5)
memory usage: 1.1+ MB


## 원핫인코딩

In [20]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(df['HomePlanet'])
df=df.drop('HomePlanet',axis=1)
df = df.join(train_encoding)

train_encoding = pd.get_dummies(df['Destination'])
df=df.drop('Destination',axis=1)
df = df.join(train_encoding)

train_encoding = pd.get_dummies(df['Cabin1'])
df=df.drop('Cabin1',axis=1)
df = df.join(train_encoding)

In [21]:
# 데이터 확인
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 26 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Combi          11076 non-null  object 
 3   Cabin3         11076 non-null  bool   
 4   Cabin          11076 non-null  object 
 5   Age            11076 non-null  float64
 6   VIP            11076 non-null  bool   
 7   RoomService    11076 non-null  float64
 8   FoodCourt      11076 non-null  float64
 9   ShoppingMall   11076 non-null  float64
 10  Spa            11076 non-null  float64
 11  VRDeck         11076 non-null  float64
 12  Earth          11076 non-null  uint8  
 13  Europa         11076 non-null  uint8  
 14  Mars           11076 non-null  uint8  
 15  55 Cancri e    11076 non-null  uint8  
 16  PSO J318.5-22  11076 non-null  uint8  
 17  TRAPPIST-1e    11076 non-null  uint8  
 18  A     

## 스케일링

In [22]:
# 스케일링을 위한 함수 생성
col = ['Cabin2', 'Age', 'RoomService','FoodCourt','ShoppingMall','Spa','VRDeck']
def data_scaled(df, col):
    for i in col:
        data_mean = df[i].mean()
        data_std = df[i].std()
        scaled = (df[i]-data_mean)/data_std
        df[i]=scaled
    return df

In [23]:
data_scaled(df, col)

CryoSleep    Cabin2  Combi  Cabin3     Cabin       Age    VIP  \
0          False -1.171058     B0    True     B/0/P  0.707877  False   
1          False -1.171058     F0   False     F/0/S -0.329018  False   
2          False -1.171058     A0   False     A/0/S  2.021278   True   
3          False -1.171058     A0   False     A/0/S  0.293119  False   
4          False -1.169112     F1   False     F/1/S -0.882029  False   
...          ...       ...    ...     ...       ...       ...    ...   
12962       True  1.737845  G1495   False  G/1495/S  0.984383  False   
12963      False -0.630138   D278   False   D/278/S  0.984383  False   
12964      False  2.323517  F1796   False  F/1796/S  0.777004  False   
12965       True  1.739790  G1496   False  G/1496/S  0.362246  False   
12969       True  1.743682  G1498   False  G/1498/S  0.984383  False   

       RoomService  FoodCourt  ShoppingMall  ...  PSO J318.5-22  TRAPPIST-1e  \
0        -0.334616  -0.282674     -0.285975  ...              0            1   
1        -0.166861  -0.277057     -0.244125  ...              0            1   
2        -0.268437   1.949128     -0.285975  ...              0            1   
3        -0.334616   0.518053      0.335083  ...              0            1   
4         0.131712  -0.238987     -0.033199  ...              0            1   
...            ...        ...           ...  ...            ...          ...   
12962    -0.334616  -0.282674     -0.285975  ...              0            1   
12963    -0.262281  -0.282674      6.160647  ...              0            1   
12964    -0.334616   0.257177     -0.285975  ...              0            1   
12965    -0.334616  -0.282674     -0.285975  ...              0            1   
12969    -0.334616  -0.282674     -0.285975  ...              1            0   

       A  B  C  D  E  F  G  T  
0      0  1  0  0  0  0  0  0  
1      0  0  0  0  0  1  0  0  
2      1  0  0  0  0  0  0  0  
3      1  0  0  0  0  0  0  0  
4      0  0  0  0  0  1  0  0  
...   .. .. .. .. .. .. .. ..  
12962  0  0  0  0  0  0  1  0  
12963  0  0  0  1  0  0  0  0  
12964  0  0  0  0  0  1  0  0  
12965  0  0  0  0  0  0  1  0  
12969  0  0  0  0  0  0  1  0  

[11076 rows x 26 columns]

In [24]:
df.head()

CryoSleep    Cabin2 Combi  Cabin3  Cabin       Age    VIP  RoomService  \
0      False -1.171058    B0    True  B/0/P  0.707877  False    -0.334616   
1      False -1.171058    F0   False  F/0/S -0.329018  False    -0.166861   
2      False -1.171058    A0   False  A/0/S  2.021278   True    -0.268437   
3      False -1.171058    A0   False  A/0/S  0.293119  False    -0.334616   
4      False -1.169112    F1   False  F/1/S -0.882029  False     0.131712   

   FoodCourt  ShoppingMall  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  E  F  \
0  -0.282674     -0.285975  ...              0            1  0  1  0  0  0  0   
1  -0.277057     -0.244125  ...              0            1  0  0  0  0  0  1   
2   1.949128     -0.285975  ...              0            1  1  0  0  0  0  0   
3   0.518053      0.335083  ...              0            1  1  0  0  0  0  0   
4  -0.238987     -0.033199  ...              0            1  0  0  0  0  0  1   

   G  T  
0  0  0  
1  0  0  
2  0  0  
3  0  0  
4  0  0  

[5 rows x 26 columns]

## 클러스터링
- 필요없는 feature 추가로 제거한 후 진행

In [25]:
dt = df.drop(['Combi', 'Cabin'], axis=1)

In [26]:
# k_range = range(2,30)

# best_k = -1
# best_silhouette_score = -1

# for k in k_range:
#     km = KMeans(n_clusters = k, random_state=109)
#     km.fit(dt)
#     clusters= km.predict(dt)
    
#     score = silhouette_score(dt, clusters)
    
#     print('k: {}, score: {}'.format(k, score))
#     if score > best_silhouette_score:
#         best_k = k
#         best_silhouette_score = score
        
# print('\n best K: {}, best Score: {}'.format(best_k, best_silhouette_score))

- 군집화를 시켜보니 실루엣 점수가 너무 낮아서 이를 포기하고 feature 별로 분류하여 결측값을 채우기로 함

## CryoSleep 결측값 채우기
- XGBoost 활용하기

In [27]:
dt.CryoSleep.value_counts()

False    6983
True     4093
Name: CryoSleep, dtype: int64

In [28]:
dt.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 24 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Cabin3         11076 non-null  bool   
 3   Age            11076 non-null  float64
 4   VIP            11076 non-null  bool   
 5   RoomService    11076 non-null  float64
 6   FoodCourt      11076 non-null  float64
 7   ShoppingMall   11076 non-null  float64
 8   Spa            11076 non-null  float64
 9   VRDeck         11076 non-null  float64
 10  Earth          11076 non-null  uint8  
 11  Europa         11076 non-null  uint8  
 12  Mars           11076 non-null  uint8  
 13  55 Cancri e    11076 non-null  uint8  
 14  PSO J318.5-22  11076 non-null  uint8  
 15  TRAPPIST-1e    11076 non-null  uint8  
 16  A              11076 non-null  uint8  
 17  B              11076 non-null  uint8  
 18  C     

### 훈련셋 테스트셋 검증셋 분리

In [122]:
X_train, X_test, y_train, y_test = train_test_split(dt.drop(['CryoSleep'], axis=1),
                                                    dt.CryoSleep, random_state=109)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train)

### 모델 생성(그리드서치)

In [123]:
xgbo = xgb.XGBClassifier()

params = {
    'max_depth':[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18,
                 19, 20, 21, 22, 23, 24, 25, None],
    'learning_rate':[0.01, 0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4],
    'gamma':[0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5],
    'random_state':[109]
}

gs = GridSearchCV(xgbo, param_grid = params, cv = 3, refit = True,
                  n_jobs=-1)
gs.fit(X_train, y_train)

GridSearchCV(cv=3,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     gpu_id=None, grow_policy=None,
                                     importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     missing=nan, monotone_constraints=None,
                                     n_estimators=100, n_jobs=None,
                                     num_parallel_tree=None, predictor=None,
                                     random_state=None, ...),
             n_jobs=-1,
             param_grid={'gamma': [0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5],
                         'learning_rate': [0.01, 0.05, 0.1, 0.15, 0.2, 0.25,
                                           0.3, 0.35, 0.4],
                         'max_depth': [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                       14, 15, 16, 17, 18, 19, 20, 21, 22, 23,
                                       24, 25, None],
                         'random_state': [109]})

### 모델 생성(HyperOPT)

In [124]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후
# 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=bin_objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[0]	validation_0-auc:0.96561	validation_1-auc:0.96379                                                                  
[1]	validation_0-auc:0.96568	validation_1-auc:0.96333                                                                  
[2]	validation_0-auc:0.98763	validation_1-auc:0.98318                                                                  
[3]	validation_0-auc:0.98835	validation_1-auc:0.98429                                                                  
[4]	validation_0-auc:0.98846	validation_1-auc:0.98390                                                                  
[5]	validation_0-auc:0.98888	validation_1-auc:0.98402                                                                  
[6]	validation_0-auc:0.98928	validation_1-auc:0.98458                                                                  
[7]	validation_0-auc:0.98928	validation_1-auc:0.98458                                                                  
[8]	validation_0-auc:0.98928	validation_

[39]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[40]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[41]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[42]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[43]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[44]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[45]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[46]	validation_0-auc:0.99194	validation_1-auc:0.98413                                                                 
[47]	validation_0-auc:0.99194	validation

[14]	validation_0-auc:0.98691	validation_1-auc:0.98300                                                                 
[15]	validation_0-auc:0.98708	validation_1-auc:0.98299                                                                 
[16]	validation_0-auc:0.98768	validation_1-auc:0.98331                                                                 
[17]	validation_0-auc:0.98768	validation_1-auc:0.98345                                                                 
[18]	validation_0-auc:0.98774	validation_1-auc:0.98338                                                                 
[19]	validation_0-auc:0.98784	validation_1-auc:0.98337                                                                 
[20]	validation_0-auc:0.98809	validation_1-auc:0.98345                                                                 
[21]	validation_0-auc:0.98820	validation_1-auc:0.98332                                                                 
[22]	validation_0-auc:0.98820	validation

[15]	validation_0-auc:0.99521	validation_1-auc:0.98392                                                                 
[16]	validation_0-auc:0.99566	validation_1-auc:0.98387                                                                 
[17]	validation_0-auc:0.99567	validation_1-auc:0.98397                                                                 
[18]	validation_0-auc:0.99610	validation_1-auc:0.98401                                                                 
[19]	validation_0-auc:0.99610	validation_1-auc:0.98396                                                                 
[20]	validation_0-auc:0.99624	validation_1-auc:0.98384                                                                 
[21]	validation_0-auc:0.99645	validation_1-auc:0.98374                                                                 
[22]	validation_0-auc:0.99664	validation_1-auc:0.98377                                                                 
[23]	validation_0-auc:0.99690	validation

[50]	validation_0-auc:0.98745	validation_1-auc:0.98343                                                                 
[51]	validation_0-auc:0.98750	validation_1-auc:0.98357                                                                 
[52]	validation_0-auc:0.98751	validation_1-auc:0.98376                                                                 
[53]	validation_0-auc:0.98758	validation_1-auc:0.98396                                                                 
[54]	validation_0-auc:0.98775	validation_1-auc:0.98392                                                                 
[55]	validation_0-auc:0.98780	validation_1-auc:0.98397                                                                 
[56]	validation_0-auc:0.98782	validation_1-auc:0.98403                                                                 
[57]	validation_0-auc:0.98783	validation_1-auc:0.98403                                                                 
[58]	validation_0-auc:0.98783	validation

...

[31]	validation_0-auc:0.98945	validation_1-auc:0.98549                                                                 
[32]	validation_0-auc:0.98944	validation_1-auc:0.98553                                                                 
[33]	validation_0-auc:0.98941	validation_1-auc:0.98555                                                                 
[34]	validation_0-auc:0.98956	validation_1-auc:0.98548                                                                 
[35]	validation_0-auc:0.98972	validation_1-auc:0.98542                                                                 
[36]	validation_0-auc:0.98973	validation_1-auc:0.98532                                                                 
[37]	validation_0-auc:0.98969	validation_1-auc:0.98530                                                                 
[38]	validation_0-auc:0.98979	validation_1-auc:0.98519                                                                 
[39]	validation_0-auc:0.98983	validation

[18]	validation_0-auc:0.98481	validation_1-auc:0.98368                                                                 
[19]	validation_0-auc:0.98471	validation_1-auc:0.98359                                                                 
[20]	validation_0-auc:0.98471	validation_1-auc:0.98359                                                                 
[21]	validation_0-auc:0.98481	validation_1-auc:0.98360                                                                 
[22]	validation_0-auc:0.98483	validation_1-auc:0.98367                                                                 
[23]	validation_0-auc:0.98483	validation_1-auc:0.98378                                                                 
[24]	validation_0-auc:0.98482	validation_1-auc:0.98380                                                                 
[25]	validation_0-auc:0.98485	validation_1-auc:0.98373                                                                 
[26]	validation_0-auc:0.98485	validation

[21]	validation_0-auc:0.98446	validation_1-auc:0.98301                                                                 
[22]	validation_0-auc:0.98541	validation_1-auc:0.98424                                                                 
[23]	validation_0-auc:0.98541	validation_1-auc:0.98424                                                                 
[24]	validation_0-auc:0.98541	validation_1-auc:0.98423                                                                 
[25]	validation_0-auc:0.98541	validation_1-auc:0.98424                                                                 
[26]	validation_0-auc:0.98541	validation_1-auc:0.98423                                                                 
[27]	validation_0-auc:0.98542	validation_1-auc:0.98423                                                                 
[28]	validation_0-auc:0.98542	validation_1-auc:0.98423                                                                 
[29]	validation_0-auc:0.98589	validation

[50]	validation_0-auc:0.99023	validation_1-auc:0.98455                                                                 
[51]	validation_0-auc:0.99033	validation_1-auc:0.98463                                                                 
[52]	validation_0-auc:0.99033	validation_1-auc:0.98469                                                                 
[53]	validation_0-auc:0.99039	validation_1-auc:0.98454                                                                 
[54]	validation_0-auc:0.99038	validation_1-auc:0.98461                                                                 
[55]	validation_0-auc:0.99043	validation_1-auc:0.98462                                                                 
[56]	validation_0-auc:0.99052	validation_1-auc:0.98452                                                                 
[57]	validation_0-auc:0.99053	validation_1-auc:0.98453                                                                 
[58]	validation_0-auc:0.99060	validation

[31]	validation_0-auc:0.98569	validation_1-auc:0.98382                                                                 
[32]	validation_0-auc:0.98572	validation_1-auc:0.98382                                                                 
[33]	validation_0-auc:0.98577	validation_1-auc:0.98386                                                                 
[34]	validation_0-auc:0.98579	validation_1-auc:0.98387                                                                 
[35]	validation_0-auc:0.98585	validation_1-auc:0.98377                                                                 
[36]	validation_0-auc:0.98583	validation_1-auc:0.98378                                                                 
[37]	validation_0-auc:0.98589	validation_1-auc:0.98368                                                                 
[38]	validation_0-auc:0.98588	validation_1-auc:0.98368                                                                 
[39]	validation_0-auc:0.98588	validation

### 결과확인

In [125]:
model = gs.best_estimator_
print(model.score(X_train, y_train))
print(model.score(X_test, y_test))
print(model.score(X_val, y_val))

0.9597110754414125
0.9364391477067533
0.9321136254212807


In [136]:
# 최적의 파라미터값
print(gs.best_params_)

{'gamma': 3.5, 'learning_rate': 0.1, 'max_depth': 16, 'random_state': 109}


#### 그리드서치

In [34]:
xgbo = xgb.XGBClassifier(gamma=1.5, learning_rate=0.1, max_depth=4, random_state=109)
xgbo.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=1.5, gpu_id=-1,
              grow_policy='depthwise', importance_type=None,
              interaction_constraints='', learning_rate=0.1, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=4, max_leaves=0, min_child_weight=1, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=109, ...)

In [35]:
train_pred = xgbo.predict(X_train)
train_proba = xgbo.predict_proba(X_train)

test_pred = xgbo.predict(X_test)
test_proba = xgbo.predict_proba(X_test)

val_pred = xgbo.predict(X_val)
val_proba = xgbo.predict_proba(X_val)

In [36]:
# 평가용 함수
def  get_clf_eval(y_test, pred=None, pred_proba=None):
    confusion = confusion_matrix(y_test, pred)
    accuracy = accuracy_score(y_test, pred)
    precision = precision_score(y_test, pred)
    recall = recall_score(y_test, pred)
    f1 = f1_score(y_test, pred)
#     roc_auc = roc_auc_score(y_test, pred_proba)
    
    print('오차 행렬')
    print(confusion)
 
    print('정확도: {0:.4f}, 정밀도: {1:.4f}, \
    재현율: {2:.4f}, F1: {3:.4f}'.format(accuracy, precision, recall, f1))

##### 훈련셋 평가

In [37]:
get_clf_eval(y_train, train_pred, train_proba)

오차 행렬
[[3658  270]
 [  50 2252]]
정확도: 0.9486, 정밀도: 0.8929,     재현율: 0.9783, F1: 0.9337


##### 테스트셋 평가

In [38]:
get_clf_eval(y_test, test_pred, test_proba)

오차 행렬
[[1613  142]
 [  22  992]]
정확도: 0.9408, 정밀도: 0.8748,     재현율: 0.9783, F1: 0.9236


##### 검증셋 평가

In [39]:
get_clf_eval(y_val, val_pred, val_proba)

오차 행렬
[[1191  109]
 [  19  758]]
정확도: 0.9384, 정밀도: 0.8743,     재현율: 0.9755, F1: 0.9221


#### HyperOPT

In [40]:
xgbo = xgb.XGBClassifier(colsample_bytree=0.8365276251129549, gamma=3.67957927070578, learning_rate=0.14989523300636218,
                         max_depth=15, min_child_weight=6, random_state=109)
xgbo.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1,
              colsample_bytree=0.8365276251129549, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=3.67957927070578, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.14989523300636218, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=15, max_leaves=0, min_child_weight=6, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=109, ...)

In [41]:
train_pred = xgbo.predict(X_train)
train_proba = xgbo.predict_proba(X_train)

test_pred = xgbo.predict(X_test)
test_proba = xgbo.predict_proba(X_test)

val_pred = xgbo.predict(X_val)
val_proba = xgbo.predict_proba(X_val)

##### 훈련셋 평가

In [42]:
get_clf_eval(y_train, train_pred, train_proba)

오차 행렬
[[3676  252]
 [  50 2252]]
정확도: 0.9515, 정밀도: 0.8994,     재현율: 0.9783, F1: 0.9372


##### 테스트셋 평가

In [43]:
get_clf_eval(y_test, test_pred, test_proba)

오차 행렬
[[1621  134]
 [  30  984]]
정확도: 0.9408, 정밀도: 0.8801,     재현율: 0.9704, F1: 0.9231


##### 검증셋 평가

In [44]:
get_clf_eval(y_val, val_pred, val_proba)

오차 행렬
[[1197  103]
 [  23  754]]
정확도: 0.9393, 정밀도: 0.8798,     재현율: 0.9704, F1: 0.9229


- CryoSleep XGBoost 모델은 0.93이상의 정확도와 다른 지표도 좋아 결측값 예측에 사용하기로 함

### 결측값 예측

In [45]:
c_na = pd.read_excel('na_slp.xlsx')

In [46]:
c_na.head()

PassengerId HomePlanet  CryoSleep Cabin1  Cabin2 Combi Cabin3   Cabin  \
0     0099_02      Earth        NaN      G    12.0   G12      P  G/12/P   
1     0105_01      Earth        NaN      F    21.0   F21      P  F/21/P   
2     0110_02     Europa        NaN      B     5.0    B5      P   B/5/P   
3     0115_01       Mars        NaN      F    24.0   F24      P  F/24/P   
4     0173_01      Earth        NaN      E    11.0   E11      S  E/11/S   

   Destination   Age  VIP  RoomService  FoodCourt  ShoppingMall  Spa  VRDeck  \
0  TRAPPIST-1e   2.0  0.0          0.0        0.0           0.0  0.0     0.0   
1  TRAPPIST-1e  27.0  0.0          0.0        0.0         570.0  2.0   131.0   
2  TRAPPIST-1e  40.0  0.0          0.0      331.0           0.0  0.0  1687.0   
3  TRAPPIST-1e  26.0  0.0          0.0        0.0           0.0  0.0     0.0   
4  TRAPPIST-1e  58.0  0.0          0.0      985.0           0.0  5.0     0.0   

               Name  Transported  
0  Thewis Connelson          1.0  
1  Carry Cleachrand          0.0  
2   Aldeba Bootious          0.0  
3         Rohs Pead          1.0  
4    Hilip Grifford          1.0

In [47]:
c_na.drop(['PassengerId', 'Name', 'Transported', 'Combi', 'Cabin', 'CryoSleep'], inplace=True, axis=1)

In [48]:
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    305 non-null    object 
 1   Cabin1        306 non-null    object 
 2   Cabin2        306 non-null    float64
 3   Cabin3        306 non-null    object 
 4   Destination   304 non-null    object 
 5   Age           307 non-null    float64
 6   VIP           301 non-null    float64
 7   RoomService   307 non-null    float64
 8   FoodCourt     307 non-null    float64
 9   ShoppingMall  300 non-null    float64
 10  Spa           303 non-null    float64
 11  VRDeck        303 non-null    float64
dtypes: float64(8), object(4)
memory usage: 29.2+ KB


In [49]:
c_na['Cabin3'].replace({'P': 'True','S': 'False'}, inplace=True)

In [50]:
c_na['Cabin3'] = c_na.Cabin3.astype(bool)
c_na['VIP'] = c_na.VIP.astype(bool)
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    305 non-null    object 
 1   Cabin1        306 non-null    object 
 2   Cabin2        306 non-null    float64
 3   Cabin3        310 non-null    bool   
 4   Destination   304 non-null    object 
 5   Age           307 non-null    float64
 6   VIP           310 non-null    bool   
 7   RoomService   307 non-null    float64
 8   FoodCourt     307 non-null    float64
 9   ShoppingMall  300 non-null    float64
 10  Spa           303 non-null    float64
 11  VRDeck        303 non-null    float64
dtypes: bool(2), float64(7), object(3)
memory usage: 24.9+ KB


In [51]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(c_na['HomePlanet'])
c_na=c_na.drop('HomePlanet',axis=1)
c_na = c_na.join(train_encoding)

train_encoding = pd.get_dummies(c_na['Destination'])
c_na=c_na.drop('Destination',axis=1)
c_na = c_na.join(train_encoding)

train_encoding = pd.get_dummies(c_na['Cabin1'])
c_na=c_na.drop('Cabin1',axis=1)
c_na = c_na.join(train_encoding)

In [52]:
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 23 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Cabin2         306 non-null    float64
 1   Cabin3         310 non-null    bool   
 2   Age            307 non-null    float64
 3   VIP            310 non-null    bool   
 4   RoomService    307 non-null    float64
 5   FoodCourt      307 non-null    float64
 6   ShoppingMall   300 non-null    float64
 7   Spa            303 non-null    float64
 8   VRDeck         303 non-null    float64
 9   Earth          310 non-null    uint8  
 10  Europa         310 non-null    uint8  
 11  Mars           310 non-null    uint8  
 12  55 Cancri e    310 non-null    uint8  
 13  PSO J318.5-22  310 non-null    uint8  
 14  TRAPPIST-1e    310 non-null    uint8  
 15  A              310 non-null    uint8  
 16  B              310 non-null    uint8  
 17  C              310 non-null    uint8  
 18  D         

In [53]:
c_na_d = c_na.dropna(axis=0)

In [54]:
col = ['Cabin2', 'Age', 'RoomService','FoodCourt','ShoppingMall','Spa','VRDeck']
data_scaled(c_na, col)

Cabin2  Cabin3       Age    VIP  RoomService  FoodCourt  ShoppingMall  \
0   -1.183897    True -1.800699  False    -0.329359  -0.324266     -0.351021   
1   -1.166462    True -0.116726  False    -0.329359  -0.324266      0.975138   
2   -1.197458    True  0.758940  False    -0.329359  -0.064159     -0.351021   
3   -1.160650    True -0.184085  False    -0.329359  -0.324266     -0.351021   
4   -1.185834    True  1.971401  False    -0.329359   0.449770     -0.351021   
..        ...     ...       ...    ...          ...        ...           ...   
305  2.260524    True -0.588239  False    -0.329359  -0.324266     -0.351021   
306 -0.635657    True -0.116726  False    -0.329359   1.390402     -0.334735   
307       NaN    True  0.826299  False    -0.329359   1.245810     -0.351021   
308  2.233403    True -0.992392  False    -0.329359  -0.324266           NaN   
309 -0.525234    True  0.220068  False    -0.329359  -0.324266     -0.351021   

          Spa    VRDeck  Earth  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  \
0   -0.236142 -0.287000      1  ...              0            1  0  0  0  0   
1   -0.234693 -0.156691      1  ...              0            1  0  0  0  0   
2   -0.236142  1.391106      0  ...              0            1  0  1  0  0   
3   -0.236142 -0.287000      0  ...              0            1  0  0  0  0   
4   -0.232519 -0.287000      1  ...              0            1  0  0  0  0   
..        ...       ...    ...  ...            ...          ... .. .. .. ..   
305 -0.236142 -0.287000      0  ...              0            0  0  0  0  0   
306  1.634807 -0.268100      0  ...              0            1  0  0  1  0   
307  0.505136  0.575429      0  ...              0            1  0  0  0  0   
308  0.761649 -0.258153      1  ...              0            1  0  0  0  0   
309 -0.236142 -0.287000      0  ...              0            0  0  1  0  0   

     E  F  G  T  
0    0  0  1  0  
1    0  1  0  0  
2    0  0  0  0  
3    0  1  0  0  
4    1  0  0  0  
..  .. .. .. ..  
305  0  1  0  0  
306  0  0  0  0  
307  0  0  0  0  
308  0  1  0  0  
309  0  0  0  0  

[310 rows x 23 columns]

In [55]:
c_na.head()

Cabin2  Cabin3       Age    VIP  RoomService  FoodCourt  ShoppingMall  \
0 -1.183897    True -1.800699  False    -0.329359  -0.324266     -0.351021   
1 -1.166462    True -0.116726  False    -0.329359  -0.324266      0.975138   
2 -1.197458    True  0.758940  False    -0.329359  -0.064159     -0.351021   
3 -1.160650    True -0.184085  False    -0.329359  -0.324266     -0.351021   
4 -1.185834    True  1.971401  False    -0.329359   0.449770     -0.351021   

        Spa    VRDeck  Earth  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  E  \
0 -0.236142 -0.287000      1  ...              0            1  0  0  0  0  0   
1 -0.234693 -0.156691      1  ...              0            1  0  0  0  0  0   
2 -0.236142  1.391106      0  ...              0            1  0  1  0  0  0   
3 -0.236142 -0.287000      0  ...              0            1  0  0  0  0  0   
4 -0.232519 -0.287000      1  ...              0            1  0  0  0  0  1   

   F  G  T  
0  0  1  0  
1  1  0  0  
2  0  0  0  
3  1  0  0  
4  0  0  0  

[5 rows x 23 columns]

In [56]:
c_pred = xgbo.predict(c_na)

In [57]:
c_pred = pd.DataFrame(c_pred)

In [58]:
c_pred.value_counts()

0    310
dtype: int64

In [59]:
c_pred.to_csv('c_pred.csv')

In [60]:
c_pred_h = xgbo.predict(c_na)

In [61]:
c_pred_h = pd.DataFrame(c_pred_h)

In [62]:
c_pred_h.value_counts()

0    310
dtype: int64

## Destination  결측값 채우기

- Destination의 결측값을 채우기 위해선 원핫인코딩 전의 df이 필요함
- 따라서 원본인 data부터 시작해야한다.

### 전처리

In [63]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: bool(3), float64(8), object(5)
memory usage: 1.3+ MB


In [64]:
# 필요없는 피처들 제거
dest = data.drop(['Combi', 'Cabin', 'Transported'], axis=1)
dest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Cabin3        12970 non-null  bool   
 5   Destination   12704 non-null  object 
 6   Age           12700 non-null  float64
 7   VIP           12970 non-null  bool   
 8   RoomService   12776 non-null  float64
 9   FoodCourt     12752 non-null  float64
 10  ShoppingMall  12760 non-null  float64
 11  Spa           12754 non-null  float64
 12  VRDeck        12766 non-null  float64
dtypes: bool(3), float64(7), object(3)
memory usage: 1.0+ MB


In [65]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(dest['HomePlanet'])
dest=dest.drop('HomePlanet',axis=1)
dest = dest.join(train_encoding)

train_encoding = pd.get_dummies(dest['Cabin1'])
dest=dest.drop('Cabin1',axis=1)
dest = dest.join(train_encoding)

In [66]:
dest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 22 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   CryoSleep     12970 non-null  bool   
 1   Cabin2        12804 non-null  float64
 2   Cabin3        12970 non-null  bool   
 3   Destination   12704 non-null  object 
 4   Age           12700 non-null  float64
 5   VIP           12970 non-null  bool   
 6   RoomService   12776 non-null  float64
 7   FoodCourt     12752 non-null  float64
 8   ShoppingMall  12760 non-null  float64
 9   Spa           12754 non-null  float64
 10  VRDeck        12766 non-null  float64
 11  Earth         12970 non-null  uint8  
 12  Europa        12970 non-null  uint8  
 13  Mars          12970 non-null  uint8  
 14  A             12970 non-null  uint8  
 15  B             12970 non-null  uint8  
 16  C             12970 non-null  uint8  
 17  D             12970 non-null  uint8  
 18  E             12970 non-nu

In [67]:
dest.dropna(axis=0, inplace=True)

In [68]:
dest.isna().sum()

CryoSleep       0
Cabin2          0
Cabin3          0
Destination     0
Age             0
VIP             0
RoomService     0
FoodCourt       0
ShoppingMall    0
Spa             0
VRDeck          0
Earth           0
Europa          0
Mars            0
A               0
B               0
C               0
D               0
E               0
F               0
G               0
T               0
dtype: int64

In [69]:
dest.Destination.unique()

array(['TRAPPIST-1e', 'PSO J318.5-22', '55 Cancri e'], dtype=object)

In [70]:
# Object 타입을 숫자형으로 변경하기
# 'TRAPPIST-1e' = 0, 'PSO J318.5-22' = 1, '55 Cancri e' = 2
dest.Destination.replace({'TRAPPIST-1e':0, 'PSO J318.5-22':1, '55 Cancri e':2}, inplace=True)

- 값들의 개수를 확인해보니 TRAPPIST-1e가 너무 많음 복합샘플링을 해보기로 함

### 복합샘플링

In [71]:
from imblearn.combine import *

In [72]:
X = dest.drop('Destination', axis=1)
y = dest.Destination

In [73]:
X.shape

(11320, 21)

#### SMOTE+ENN

In [129]:
X_samp, y_samp = SMOTEENN(random_state=109).fit_resample(X, y)

In [75]:
X_samp.shape

(11882, 21)

In [76]:
dest.Destination.value_counts()

0    7894
2    2370
1    1056
Name: Destination, dtype: int64

In [77]:
y_samp.value_counts()

1    5410
2    4381
0    2091
Name: Destination, dtype: int64

#### 훈련셋 테스트셋 검증셋 분리

In [130]:
X_train, X_test, y_train, y_test = train_test_split(X_samp, y_samp, random_state=109)

#### HyperOPT

- 하이퍼파라미터가 많을수록 그리드서치는 느려지기에 HyperOPT 사용

In [79]:
# max_depth=??
xgb_search_space = {'max_depth': hp.quniform('max_depth', 5, 15, 1),
                   'min_child_weight': hp.quniform('min_child_weight', 1, 20, 1),
                   'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 0.95),
                   'learning_rate': hp.uniform('learning_rate', 0.01, 0.4),
                   'gamma': hp.uniform('gamma', 0, 4)}

In [127]:
# fmin()에서 호출 시 search_space 값으로 XGBClassifier 교차 검증 학습 후 -1 * roc_auc 평균 값을 반환
def objective_func(search_space):
    xgb_clf = xgb.XGBClassifier(n_estimators=100, max_depth=int(search_space['max_depth']),
                            min_child_weight=int(search_space['min_child_weight']),
                            colsample_bytree=search_space['colsample_bytree'],
                            learning_rate=search_space['learning_rate'],
                            gamma=search_space['gamma'])
    
    # 3개 k-fold 방식으로 평가된 roc_auc 지표를 담는 list
    roc_auc_list = []
    
    # 3개 k-fold 방식 적용
    kf = KFold(n_splits=3)
    
    # X_train을 다시 학습과 검증용 데이터로 분리
    for tr_index, val_index in kf.split(X_train):
        # kf.split(X_train)으로 추출된 학습과 검증 index 값으로 학습과 검증 데이터 세트 분리
        X_tr, y_tr = X_train.iloc[tr_index], y_train.iloc[tr_index]
        X_val, y_val = X_train.iloc[val_index], y_train.iloc[val_index]
        
        # early stopping은 30회로 설정하고 추출된 학습과 검증 데이터로 XGBClassifier 학습 수행
        xgb_clf.fit(X_tr, y_tr, early_stopping_rounds=30, eval_metric="auc",
                   eval_set=[(X_tr, y_tr), (X_val, y_val)])
        
        # 1로 예측한 확률값 추출 후 roc auc 계산하고 평균 roc auc 계산을 위해 list에 결과값 담음.
        score = roc_auc_score(y_val, xgb_clf.predict_proba(X_val)[:,:], multi_class='ovo')
        roc_auc_list.append(score)
        
    # 3개 k-fold로 계산된 roc_auc 값의 평균값을 반환하되,
    # HyperOPT는 목적함수의 최솟값을 위한 입력값을 찾으므로 -1을 곱한 뒤 반환
    return -1*np.mean(roc_auc_list)

In [131]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정합니다
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[0]	validation_0-auc:0.93937	validation_1-auc:0.90649                                                                  
[1]	validation_0-auc:0.95190	validation_1-auc:0.91653                                                                  
[2]	validation_0-auc:0.95830	validation_1-auc:0.92043                                                                  
[3]	validation_0-auc:0.96141	validation_1-auc:0.92290                                                                  
[4]	validation_0-auc:0.96278	validation_1-auc:0.92423                                                                  
[5]	validation_0-auc:0.96512	validation_1-auc:0.92704                                                                  
[6]	validation_0-auc:0.96571	validation_1-auc:0.92889                                                                  
[7]	validation_0-auc:0.96784	validation_1-auc:0.93144                                                                  
[8]	validation_0-auc:0.97063	validation_

[36]	validation_0-auc:0.98483	validation_1-auc:0.94587                                                                 
[37]	validation_0-auc:0.98489	validation_1-auc:0.94610                                                                 
[38]	validation_0-auc:0.98491	validation_1-auc:0.94605                                                                 
[39]	validation_0-auc:0.98532	validation_1-auc:0.94638                                                                 
[40]	validation_0-auc:0.98533	validation_1-auc:0.94638                                                                 
[41]	validation_0-auc:0.98546	validation_1-auc:0.94657                                                                 
[42]	validation_0-auc:0.98554	validation_1-auc:0.94663                                                                 
[43]	validation_0-auc:0.98564	validation_1-auc:0.94656                                                                 
[44]	validation_0-auc:0.98596	validation

[72]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[73]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[74]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[75]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[76]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[77]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[78]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[79]	validation_0-auc:0.98708	validation_1-auc:0.95252                                                                 
[80]	validation_0-auc:0.98708	validation

[9]	validation_0-auc:0.93356	validation_1-auc:0.90824                                                                  
[10]	validation_0-auc:0.93582	validation_1-auc:0.90975                                                                 
[11]	validation_0-auc:0.93610	validation_1-auc:0.90999                                                                 
[12]	validation_0-auc:0.93824	validation_1-auc:0.91117                                                                 
[13]	validation_0-auc:0.93970	validation_1-auc:0.91201                                                                 
[14]	validation_0-auc:0.94021	validation_1-auc:0.91249                                                                 
[15]	validation_0-auc:0.94078	validation_1-auc:0.91321                                                                 
[16]	validation_0-auc:0.94193	validation_1-auc:0.91439                                                                 
[17]	validation_0-auc:0.94292	validation

[45]	validation_0-auc:0.95811	validation_1-auc:0.93377                                                                 
[46]	validation_0-auc:0.95833	validation_1-auc:0.93396                                                                 
[47]	validation_0-auc:0.95879	validation_1-auc:0.93438                                                                 
[48]	validation_0-auc:0.95925	validation_1-auc:0.93481                                                                 
[49]	validation_0-auc:0.95967	validation_1-auc:0.93485                                                                 
[50]	validation_0-auc:0.96024	validation_1-auc:0.93509                                                                 
[51]	validation_0-auc:0.96054	validation_1-auc:0.93522                                                                 
[52]	validation_0-auc:0.96077	validation_1-auc:0.93534                                                                 
[53]	validation_0-auc:0.96118	validation

...

[36]	validation_0-auc:0.99127	validation_1-auc:0.95046                                                                 
[37]	validation_0-auc:0.99164	validation_1-auc:0.95094                                                                 
[38]	validation_0-auc:0.99204	validation_1-auc:0.95125                                                                 
[39]	validation_0-auc:0.99233	validation_1-auc:0.95173                                                                 
[40]	validation_0-auc:0.99269	validation_1-auc:0.95183                                                                 
[41]	validation_0-auc:0.99294	validation_1-auc:0.95204                                                                 
[42]	validation_0-auc:0.99310	validation_1-auc:0.95214                                                                 
[43]	validation_0-auc:0.99345	validation_1-auc:0.95256                                                                 
[44]	validation_0-auc:0.99369	validation

[72]	validation_0-auc:0.99607	validation_1-auc:0.95499                                                                 
[73]	validation_0-auc:0.99618	validation_1-auc:0.95510                                                                 
[74]	validation_0-auc:0.99628	validation_1-auc:0.95522                                                                 
[75]	validation_0-auc:0.99636	validation_1-auc:0.95540                                                                 
[76]	validation_0-auc:0.99643	validation_1-auc:0.95554                                                                 
[77]	validation_0-auc:0.99649	validation_1-auc:0.95567                                                                 
[78]	validation_0-auc:0.99655	validation_1-auc:0.95577                                                                 
[79]	validation_0-auc:0.99660	validation_1-auc:0.95599                                                                 
[80]	validation_0-auc:0.99665	validation

[8]	validation_0-auc:0.93332	validation_1-auc:0.90769                                                                  
[9]	validation_0-auc:0.93385	validation_1-auc:0.90828                                                                  
[10]	validation_0-auc:0.93536	validation_1-auc:0.90962                                                                 
[11]	validation_0-auc:0.93610	validation_1-auc:0.91046                                                                 
[12]	validation_0-auc:0.93664	validation_1-auc:0.91079                                                                 
[13]	validation_0-auc:0.93704	validation_1-auc:0.91096                                                                 
[14]	validation_0-auc:0.93754	validation_1-auc:0.91143                                                                 
[15]	validation_0-auc:0.93800	validation_1-auc:0.91202                                                                 
[16]	validation_0-auc:0.93886	validation

[44]	validation_0-auc:0.94672	validation_1-auc:0.91699                                                                 
[45]	validation_0-auc:0.94669	validation_1-auc:0.91695                                                                 
[46]	validation_0-auc:0.94684	validation_1-auc:0.91709                                                                 
[47]	validation_0-auc:0.94706	validation_1-auc:0.91734                                                                 
[48]	validation_0-auc:0.94717	validation_1-auc:0.91735                                                                 
[49]	validation_0-auc:0.94725	validation_1-auc:0.91739                                                                 
[50]	validation_0-auc:0.94758	validation_1-auc:0.91786                                                                 
[51]	validation_0-auc:0.94762	validation_1-auc:0.91783                                                                 
[52]	validation_0-auc:0.94779	validation

[80]	validation_0-auc:0.94824	validation_1-auc:0.92648                                                                 
[81]	validation_0-auc:0.94828	validation_1-auc:0.92655                                                                 
[82]	validation_0-auc:0.94858	validation_1-auc:0.92673                                                                 
[83]	validation_0-auc:0.94865	validation_1-auc:0.92676                                                                 
[84]	validation_0-auc:0.94889	validation_1-auc:0.92680                                                                 
[85]	validation_0-auc:0.94921	validation_1-auc:0.92705                                                                 
[86]	validation_0-auc:0.94937	validation_1-auc:0.92712                                                                 
[87]	validation_0-auc:0.94952	validation_1-auc:0.92718                                                                 
[88]	validation_0-auc:0.94966	validation

#### 최적합 모델 생성

In [82]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.7509517286334861, gamma=0.1340433243883299,
                            learning_rate=0.1876055512521753, max_depth=13,
                            min_child_weight=4.0,random_state=109)
xgb_clf.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1,
              colsample_bytree=0.7509517286334861, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.1340433243883299, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.1876055512521753, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=13, max_leaves=0, min_child_weight=4.0, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, objective='multi:softprob', predictor='auto', ...)

In [83]:
train_pred = xgb_clf.predict(X_train)
train_proba = xgb_clf.predict_proba(X_train)

test_pred = xgb_clf.predict(X_test)
test_proba = xgb_clf.predict_proba(X_test)

#### 결과확인

##### 훈련셋 평가

In [84]:
confusion_matrix(y_train, train_pred)

array([[1545,   27,   12],
       [   1, 4005,    8],
       [   0,   39, 3274]], dtype=int64)

In [85]:
accuracy_score(y_train, train_pred)

0.9902367859948379

In [86]:
recall_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.9902367859948379

In [87]:
precision_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.9902367859948379

##### 테스트셋 평가

In [90]:
confusion_matrix(y_test, test_pred)

array([[ 381,   62,   64],
       [  35, 1337,   24],
       [  46,   95,  927]], dtype=int64)

In [91]:
accuracy_score(y_test, test_pred)

0.8902726354762707

#### SMOTE+Tomek

In [132]:
X_samp, y_samp = SMOTETomek(random_state=109).fit_resample(X, y)

In [93]:
y.value_counts()

0    7894
2    2370
1    1056
Name: Destination, dtype: int64

In [94]:
y_samp.value_counts()

1    7435
2    7330
0    7069
Name: Destination, dtype: int64

#### 훈련셋 테스트셋 검증셋 분리

In [133]:
X_train, X_test, y_train, y_test = train_test_split(X_samp, y_samp, random_state=109)

#### HyperOPT

In [134]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정합니다
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[0]	validation_0-auc:0.88882	validation_1-auc:0.84630                                                                  
[1]	validation_0-auc:0.90595	validation_1-auc:0.86143                                                                  
[2]	validation_0-auc:0.91407	validation_1-auc:0.86867                                                                  
[3]	validation_0-auc:0.92016	validation_1-auc:0.87461                                                                  
[4]	validation_0-auc:0.92452	validation_1-auc:0.87795                                                                  
[5]	validation_0-auc:0.92935	validation_1-auc:0.88110                                                                  
[6]	validation_0-auc:0.93256	validation_1-auc:0.88307                                                                  
[7]	validation_0-auc:0.93497	validation_1-auc:0.88528                                                                  
[8]	validation_0-auc:0.93778	validation_

[36]	validation_0-auc:0.96440	validation_1-auc:0.90957                                                                 
[37]	validation_0-auc:0.96441	validation_1-auc:0.90963                                                                 
[38]	validation_0-auc:0.96476	validation_1-auc:0.91015                                                                 
[39]	validation_0-auc:0.96501	validation_1-auc:0.91024                                                                 
[40]	validation_0-auc:0.96525	validation_1-auc:0.91061                                                                 
[41]	validation_0-auc:0.96549	validation_1-auc:0.91070                                                                 
[42]	validation_0-auc:0.96560	validation_1-auc:0.91076                                                                 
[43]	validation_0-auc:0.96580	validation_1-auc:0.91134                                                                 
[44]	validation_0-auc:0.96588	validation

[72]	validation_0-auc:0.96636	validation_1-auc:0.90804                                                                 
[73]	validation_0-auc:0.96636	validation_1-auc:0.90804                                                                 
[74]	validation_0-auc:0.96679	validation_1-auc:0.90825                                                                 
[75]	validation_0-auc:0.96693	validation_1-auc:0.90845                                                                 
[76]	validation_0-auc:0.96699	validation_1-auc:0.90847                                                                 
[77]	validation_0-auc:0.96708	validation_1-auc:0.90843                                                                 
[78]	validation_0-auc:0.96751	validation_1-auc:0.90870                                                                 
[79]	validation_0-auc:0.96782	validation_1-auc:0.90877                                                                 
[80]	validation_0-auc:0.96866	validation

[8]	validation_0-auc:0.87742	validation_1-auc:0.85533                                                                  
[9]	validation_0-auc:0.87915	validation_1-auc:0.85693                                                                  
[10]	validation_0-auc:0.88106	validation_1-auc:0.85794                                                                 
[11]	validation_0-auc:0.88269	validation_1-auc:0.85955                                                                 
[12]	validation_0-auc:0.88436	validation_1-auc:0.86070                                                                 
[13]	validation_0-auc:0.88561	validation_1-auc:0.86142                                                                 
[14]	validation_0-auc:0.88678	validation_1-auc:0.86196                                                                 
[15]	validation_0-auc:0.88762	validation_1-auc:0.86280                                                                 
[16]	validation_0-auc:0.88944	validation

[44]	validation_0-auc:0.91907	validation_1-auc:0.88098                                                                 
[45]	validation_0-auc:0.91973	validation_1-auc:0.88144                                                                 
[46]	validation_0-auc:0.92054	validation_1-auc:0.88175                                                                 
[47]	validation_0-auc:0.92141	validation_1-auc:0.88219                                                                 
[48]	validation_0-auc:0.92171	validation_1-auc:0.88234                                                                 
[49]	validation_0-auc:0.92214	validation_1-auc:0.88251                                                                 
[50]	validation_0-auc:0.92251	validation_1-auc:0.88277                                                                 
[51]	validation_0-auc:0.92324	validation_1-auc:0.88333                                                                 
[52]	validation_0-auc:0.92364	validation

...

[21]	validation_0-auc:0.88271	validation_1-auc:0.86076                                                                 
[22]	validation_0-auc:0.88376	validation_1-auc:0.86120                                                                 
[23]	validation_0-auc:0.88477	validation_1-auc:0.86195                                                                 
[24]	validation_0-auc:0.88592	validation_1-auc:0.86262                                                                 
[25]	validation_0-auc:0.88733	validation_1-auc:0.86368                                                                 
[26]	validation_0-auc:0.88837	validation_1-auc:0.86462                                                                 
[27]	validation_0-auc:0.88945	validation_1-auc:0.86494                                                                 
[28]	validation_0-auc:0.89034	validation_1-auc:0.86563                                                                 
[29]	validation_0-auc:0.89101	validation

[57]	validation_0-auc:0.91919	validation_1-auc:0.88596                                                                 
[58]	validation_0-auc:0.91995	validation_1-auc:0.88599                                                                 
[59]	validation_0-auc:0.92062	validation_1-auc:0.88643                                                                 
[60]	validation_0-auc:0.92144	validation_1-auc:0.88673                                                                 
[61]	validation_0-auc:0.92233	validation_1-auc:0.88723                                                                 
[62]	validation_0-auc:0.92294	validation_1-auc:0.88764                                                                 
[63]	validation_0-auc:0.92389	validation_1-auc:0.88792                                                                 
[64]	validation_0-auc:0.92430	validation_1-auc:0.88807                                                                 
[65]	validation_0-auc:0.92518	validation

[93]	validation_0-auc:0.94359	validation_1-auc:0.89403                                                                 
[94]	validation_0-auc:0.94413	validation_1-auc:0.89420                                                                 
[95]	validation_0-auc:0.94457	validation_1-auc:0.89456                                                                 
[96]	validation_0-auc:0.94507	validation_1-auc:0.89488                                                                 
[97]	validation_0-auc:0.94540	validation_1-auc:0.89509                                                                 
[98]	validation_0-auc:0.94593	validation_1-auc:0.89542                                                                 
[99]	validation_0-auc:0.94643	validation_1-auc:0.89558                                                                 
[0]	validation_0-auc:0.89220	validation_1-auc:0.85896                                                                  
[1]	validation_0-auc:0.90309	validation_

[29]	validation_0-auc:0.93951	validation_1-auc:0.89230                                                                 
[30]	validation_0-auc:0.94028	validation_1-auc:0.89271                                                                 
[31]	validation_0-auc:0.94080	validation_1-auc:0.89302                                                                 
[32]	validation_0-auc:0.94168	validation_1-auc:0.89342                                                                 
[33]	validation_0-auc:0.94267	validation_1-auc:0.89408                                                                 
[34]	validation_0-auc:0.94307	validation_1-auc:0.89433                                                                 
[35]	validation_0-auc:0.94429	validation_1-auc:0.89517                                                                 
[36]	validation_0-auc:0.94483	validation_1-auc:0.89551                                                                 
[37]	validation_0-auc:0.94527	validation

[65]	validation_0-auc:0.95760	validation_1-auc:0.90194                                                                 
[66]	validation_0-auc:0.95788	validation_1-auc:0.90226                                                                 
[67]	validation_0-auc:0.95833	validation_1-auc:0.90253                                                                 
[68]	validation_0-auc:0.95867	validation_1-auc:0.90292                                                                 
[69]	validation_0-auc:0.95886	validation_1-auc:0.90315                                                                 
[70]	validation_0-auc:0.95919	validation_1-auc:0.90333                                                                 
[71]	validation_0-auc:0.95957	validation_1-auc:0.90366                                                                 
[72]	validation_0-auc:0.95991	validation_1-auc:0.90404                                                                 
[73]	validation_0-auc:0.96015	validation

#### 최적합 모델 생성

In [97]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.8225370817776354, gamma=0.5234281986576236,
                            learning_rate=0.2851568524972954, max_depth=11,
                            min_child_weight=2,random_state=109)
xgb_clf.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1,
              colsample_bytree=0.8225370817776354, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.5234281986576236, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.2851568524972954, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=11, max_leaves=0, min_child_weight=2, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, objective='multi:softprob', predictor='auto', ...)

#### 결과확인

In [98]:
train_pred = xgb_clf.predict(X_train)
train_proba = xgb_clf.predict_proba(X_train)

test_pred = xgb_clf.predict(X_test)
test_proba = xgb_clf.predict_proba(X_test)

##### 훈련셋

In [99]:
confusion_matrix(y_train, train_pred)

array([[5128,  101,   86],
       [  42, 5519,   15],
       [ 126,  141, 5217]], dtype=int64)

In [100]:
accuracy_score(y_train, train_pred)

0.968793893129771

In [101]:
recall_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.968793893129771

In [102]:
precision_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.968793893129771

##### 테스트셋

In [103]:
confusion_matrix(y_test, test_pred)

array([[1374,  157,  223],
       [ 132, 1676,   51],
       [ 319,  177, 1350]], dtype=int64)

In [104]:
accuracy_score(y_test, test_pred)

0.8060084264517311

In [105]:
recall_score(y_test, test_pred, labels=[0, 1, 2], average='micro')

0.8060084264517311

In [106]:
precision_score(y_test, test_pred, labels=[0, 1, 2], average='micro')

0.8060084264517311

## VIP 추가

In [107]:
X_v = dt.drop('VIP', axis=1)
y_v = dt.VIP

In [108]:
X_v.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 23 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Cabin3         11076 non-null  bool   
 3   Age            11076 non-null  float64
 4   RoomService    11076 non-null  float64
 5   FoodCourt      11076 non-null  float64
 6   ShoppingMall   11076 non-null  float64
 7   Spa            11076 non-null  float64
 8   VRDeck         11076 non-null  float64
 9   Earth          11076 non-null  uint8  
 10  Europa         11076 non-null  uint8  
 11  Mars           11076 non-null  uint8  
 12  55 Cancri e    11076 non-null  uint8  
 13  PSO J318.5-22  11076 non-null  uint8  
 14  TRAPPIST-1e    11076 non-null  uint8  
 15  A              11076 non-null  uint8  
 16  B              11076 non-null  uint8  
 17  C              11076 non-null  uint8  
 18  D     

In [109]:
y_v

0        False
1        False
2         True
3        False
4        False
         ...  
12962    False
12963    False
12964    False
12965    False
12969    False
Name: VIP, Length: 11076, dtype: bool

In [110]:
X_vsamp, y_vsamp = SMOTEENN(random_state=109).fit_resample(X_v, y_v)

In [111]:
y_v.shape

(11076,)

In [112]:
y_v.value_counts()

False    10584
True       492
Name: VIP, dtype: int64

In [113]:
X_train, X_test, y_train, y_test = train_test_split(X_vsamp, y_vsamp, random_state=109)

In [114]:
# fmin()에서 호출 시 search_space 값으로 XGBClassifier 교차 검증 학습 후 -1 * roc_auc 평균 값을 반환
def bin_objective_func(search_space):
    xgb_clf = xgb.XGBClassifier(n_estimators=100, max_depth=int(search_space['max_depth']),
                            min_child_weight=int(search_space['min_child_weight']),
                            colsample_bytree=search_space['colsample_bytree'],
                            learning_rate=search_space['learning_rate'],
                            gamma=search_space['gamma'])
    
    # 3개 k-fold 방식으로 평가된 roc_auc 지표를 담는 list
    roc_auc_list = []
    
    # 3개 k-fold 방식 적용
    kf = KFold(n_splits=3)
    
    # X_train을 다시 학습과 검증용 데이터로 분리
    for tr_index, val_index in kf.split(X_train):
        # kf.split(X_train)으로 추출된 학습과 검증 index 값으로 학습과 검증 데이터 세트 분리
        X_tr, y_tr = X_train.iloc[tr_index], y_train.iloc[tr_index]
        X_val, y_val = X_train.iloc[val_index], y_train.iloc[val_index]
        
        # early stopping은 30회로 설정하고 추출된 학습과 검증 데이터로 XGBClassifier 학습 수행
        xgb_clf.fit(X_tr, y_tr, early_stopping_rounds=30, eval_metric="auc",
                   eval_set=[(X_tr, y_tr), (X_val, y_val)])
        
        # 1로 예측한 확률값 추출 후 roc auc 계산하고 평균 roc auc 계산을 위해 list에 결과값 담음.
        score = roc_auc_score(y_val, xgb_clf.predict_proba(X_val)[:,1])
        roc_auc_list.append(score)
        
    # 3개 k-fold로 계산된 roc_auc 값의 평균값을 반환하되,
    # HyperOPT는 목적함수의 최솟값을 위한 입력값을 찾으므로 -1을 곱한 뒤 반환
    return -1*np.mean(roc_auc_list)

In [115]:
# trials = Trials()

# # fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
# best = fmin(fn=bin_objective_func,
#            space=xgb_search_space,
#            algo=tpe.suggest,
#            max_evals=50, # 최대 반복 횟수를 지정합니다
#            trials=trials, rstate=np.random.default_rng(seed=109))

# print('best:', best)

In [116]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.7458564543464659, gamma=0.11238303917591316,
                            learning_rate=0.37018445848424064, max_depth=13, min_child_weight=1.0,
                            random_state=109)
xgb_clf.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1,
              colsample_bytree=0.7458564543464659, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.11238303917591316, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.37018445848424064, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=13, max_leaves=0, min_child_weight=1.0, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=109, ...)

In [117]:
train_pred = xgb_clf.predict(X_train)
train_proba = xgb_clf.predict_proba(X_train)

test_pred = xgb_clf.predict(X_test)
test_proba = xgb_clf.predict_proba(X_test)

In [118]:
get_clf_eval(y_train, train_pred, train_proba)

오차 행렬
[[6043    0]
 [   0 7130]]
정확도: 1.0000, 정밀도: 1.0000,     재현율: 1.0000, F1: 1.0000


In [119]:
get_clf_eval(y_test, test_pred, test_proba)

오차 행렬
[[2000   65]
 [  67 2260]]
정확도: 0.9699, 정밀도: 0.9720,     재현율: 0.9712, F1: 0.9716
